In [ ]:
import pylab as plt
import numpy as np
from netCDF4 import Dataset
import xarray as xr
import sys as sys
import glob as glob
import matplotlib.pyplot as plt
import matplotlib as mpl
import matplotlib.colors as mcolors
import datetime
from scipy import ndimage
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
from wave_physics_functions import wavespec_Efth_to_Ekxky,wavespec_Efth_to_first3

from matplotlib.pyplot import cm
import pickle
from scipy import signal
import scipy.signal as sg


#PATH_with_functions = '/home/ardhuin/TOOLS/OPTOOLS/PYTHON/'
#sys.path.append(PATH_with_functions)
from  spectral_analysis_functions import *
plt.rcParams.update({'font.size': 18,'savefig.facecolor':'white'})

cNorm = mcolors.Normalize(vmin=0, vmax=2)
jet = plt.get_cmap('jet')
mpl.rcParams.update({'figure.figsize':[10,6],'axes.grid' : True,'font.size': 14,'savefig.facecolor':'white'})


In [ ]:
from SEAScope.lib.utils import create_collection, init_ids
from SEAScope.lib.utils import create_granule
import SEAScope.upload
from SEAScope.lib.utils import set_field
from SEAScope.lib.utils import create_variable
# Load data directly from viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()
## Print a list of path of extracted granules 
print('\n'.join(extractions.keys()))
# Get longitudes, latitudes from gcps and time from first granule
granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == 0)
extraction = extractions[granule_uri]
start = extraction['meta']['start']
print(extraction['meta']['fields'])


In [ ]:
import numpy
# name_var_tp = 'VTM01_SW1'
name_var_ssh = 'ssh_karin_2_nolr'
name_var_ssr = 'roughness_sig0_karin_2'
granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == 0)
extraction = extractions[granule_uri]   
# tp = extraction['data'][name_var_tp]

# granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == 1)
# extraction = extractions[granule_uri]   
ssh = extraction['data'][name_var_ssh]
# ssr = extraction['data']['sea_surface_roughness']
# granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == 1)
# extraction = extractions[granule_uri]   
ssr = extraction['data'][name_var_ssr]

from SEAScope.lib.utils import get_lonlat
lon2D, lat2D = get_lonlat(extraction, numpy.shape(ssh))


In [ ]:
crop = 40
ssr_crop = ssr[crop:-crop, crop:-crop]
ssh_crop = ssh[crop:-crop, crop:-crop]
fig = plt.figure(figsize=(16,10))
plt.imshow(numpy.flipud(ssr_crop),interpolation='bicubic',cmap='gray')
cbar = plt.colorbar()
cbar.ax.set_ylabel('relative Sea Surface Roughness inverted from sigma0')

In [ ]:
# define the numbers of pixels to crop from the border (will be applied to crop left, right, up, down)
fig = plt.figure(figsize=(12,10))
plt.imshow(numpy.flipud(ssh_crop*100),interpolation='bicubic',cmap='gray')
cbar = plt.colorbar()
cbar.ax.set_ylabel('SSH high pass filtered at 5km (cm)')

In [ ]:
import geopy.distance
coords_1 = (lat2D[int(ssh.shape[0]/2+1), int(ssh.shape[1]/2)],lon2D[int(ssh.shape[0]/2+1), int(ssh.shape[1]/2)])
coords_2 = (lat2D[int(ssh.shape[0]/2),int(ssh.shape[1]/2)],lon2D[int(ssh.shape[0]/2),int(ssh.shape[1]/2)])
print(geopy.distance.geodesic(coords_1, coords_2).m)
ground_spacing = geopy.distance.geodesic(coords_1, coords_2).m

In [ ]:
from numpy.fft import fft2, fftshift, ifft2, fftfreq
import math

In [ ]:
def rebin(a, shape):
    sh = shape[0],a.shape[0]//shape[0],shape[1],a.shape[1]//shape[1]
    return a.reshape(sh).mean(-1).mean(1)

In [ ]:
def looks2xspec(im1,im2,periodo_size):
    imshape = numpy.array(im1.shape, dtype='int32')

    ###########################################################################
    # Set periodograms/looks/specs sizes and positions
    ###########################################################################

    aziwindow = numpy.hanning(periodo_size+2)[1:-1]
    ranwindow = numpy.hanning(periodo_size+2)[1:-1]
    window = numpy.sqrt(numpy.outer(aziwindow, ranwindow))
    ###########################################################################
    # Compute periodograms and compute co/cross spectra
    ###########################################################################

    count = numpy.ceil(imshape[0]/periodo_size).astype('int32')
    perpos = (numpy.floor(numpy.linspace(0, imshape[0]-periodo_size, num=count)+0.5).astype('int32'),
              numpy.floor(numpy.linspace(0, imshape[1]-periodo_size, num=count)+0.5).astype('int32'))
    specshape = numpy.array((periodo_size, periodo_size), dtype='int32')
    specs = numpy.zeros(specshape, dtype='complex64')

    for appos in iter(perpos[0]):
        for rppos in iter(perpos[1]):
            sub1 = im1[appos:appos+periodo_size, rppos:rppos+periodo_size]
            sub1 = sub1 - numpy.mean(sub1)
            per1 = fftshift(fft2(sub1*window))/periodo_size
            sub2 = im2[appos:appos+periodo_size, rppos:rppos+periodo_size]
            sub2 = sub2 - numpy.mean(sub2)
            per2 = fftshift(fft2(sub2*window))/periodo_size
            specs += per1 * numpy.conj(per2)
            
    specs[int(periodo_size/2-2):int(periodo_size/2+3), int(periodo_size/2-2):int(periodo_size/2+3)] = 0
    specs[int(periodo_size/2-3):int(periodo_size/2+4), int(periodo_size/2)] = 0
    specs[int(periodo_size/2), int(periodo_size/2-3):int(periodo_size/2+4)] = 0
    
    return specs

In [ ]:
# Define period to compute spectrum
periodo_size = 256
dkran = 2*numpy.pi/(periodo_size*ground_spacing)
dkazi = dkran
spec = looks2xspec(ssh_crop, ssh_crop,periodo_size)
spec = spec*np.var(ssh_crop)/np.sum(np.abs(spec))/dkran/dkazi

In [ ]:
ssrspec = looks2xspec(ssr_crop, ssr_crop,periodo_size)
ssrspec = ssrspec*np.var(ssr_crop)/np.sum(np.abs(ssrspec))/dkran/dkazi
xspec = looks2xspec(ssh_crop, ssr_crop,periodo_size)
xspec = xspec*np.sqrt(np.var(ssh_crop)*np.var(ssr_crop))/np.sum(np.abs(xspec))/dkran/dkazi
coh = np.abs(xspec)**2/spec/ssrspec/2

In [ ]:
kran = (numpy.arange(periodo_size)-(periodo_size-1)/2.)/periodo_size*2*numpy.pi/ground_spacing
kazi = (numpy.arange(periodo_size)-(periodo_size-1)/2.)/periodo_size*2*numpy.pi/ground_spacing
fig = plt.figure(figsize = (12,10))
pi = numpy.pi
ct=2.85
cut = int(periodo_size/ct)
from scipy.signal import medfilt
# plt.imshow(numpy.flipud(numpy.abs(spec[cut:-cut+1,cut:-cut-1])*1e-5), extent=[kran[0+cut], kran[-1-cut],
#             kazi[-1-cut], kazi[1+cut]], aspect='auto',cmap='jet')
plt.imshow(numpy.log(numpy.flipud(numpy.abs(spec[cut:-cut+1,cut:-cut+1]))), extent=[kran[cut-1], kran[-cut],
            kazi[-cut], kazi[cut-1]], aspect='auto',cmap='jet')

kcircle=[2*pi/1000,2*pi/800, 2*pi/600, 2*pi/500]#, 2*pi/400]#, 2*pi/200]#, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':b')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.001), kcirstr, ha='center', va='top',fontsize=None,color='black')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('SSH spec                                      ')
cbar = plt.colorbar()
cbar.ax.set_ylabel('log scale')

In [ ]:
fig = plt.figure(figsize = (12,10))
cut = int(periodo_size/ct)
plt.imshow(np.log(numpy.flipud(numpy.abs(ssrspec[cut:-cut+1,cut:-cut+1]))), extent=[kran[cut-1], kran[-cut],
            kazi[-cut], kazi[cut-1]], aspect='auto',cmap='jet')

kcircle=[2*pi/1000,2*pi/800, 2*pi/600, 2*pi/500]#, 2*pi/200]#, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':k')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.001), kcirstr, ha='center', va='top',fontsize=None,color='k')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('SSR spec                                      ')
cbar = plt.colorbar()
cbar.ax.set_ylabel('log scale')

In [ ]:
fig = plt.figure(figsize = (12,10))
cut = int(periodo_size/ct)
plt.imshow(np.log(numpy.flipud(numpy.abs(xspec[cut:-cut+1,cut:-cut+1]))), extent=[kran[cut-1], kran[-cut],
            kazi[-cut], kazi[cut-1]], aspect='auto',cmap='jet')

kcircle=[2*pi/1000,2*pi/800, 2*pi/600, 2*pi/500]#, 2*pi/200]#, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':k')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.001), kcirstr, ha='center', va='top',fontsize=None,color='k')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('SSH SSR Xspec                                      ')
cbar = plt.colorbar()
cbar.ax.set_ylabel('lin scale')

In [ ]:
fig = plt.figure(figsize = (12,10))
cut = int(periodo_size/ct)
cohf = scipy.ndimage.gaussian_filter(coh, 1)
from scipy.signal import medfilt
cohf = medfilt(np.abs(coh), 7)
plt.imshow((numpy.flipud(numpy.abs(cohf[cut:-cut+1,cut:-cut+1]))), extent=[kran[cut-1], kran[-cut],
            kazi[-cut], kazi[cut-1]], aspect='auto',cmap='jet', vmax = 1)

kcircle=[2*pi/1000,2*pi/800, 2*pi/600, 2*pi/500]#, 2*pi/200]#, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':w')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.001), kcirstr, ha='center', va='top',fontsize=None,color='white')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('SSH SSR Coherence')
cbar = plt.colorbar()
cbar.ax.set_ylabel('lin scale')

In [ ]:
def get_obp_filter(L_filt = 1, sampling_in = 0.025, f_axis = None, plot_flag = True, kernel="parzen"):
    """
    Get the kernel shape and the spectral response of the filter type specified in the arguments
    
    Arguments:
    L_filt,      Kernel length in km
    sampling_in, Spatial spacing (in km) of the filter kernel
    f_axis,      Frequency axis where to compute the spectral response of the filter
    plot_flag,   Plot filter kernel and spectral response
    kernel,      Kernel to compute ('parzen' or 'bharris' -for Blackman-Harris)
    """
    Nparzen = int(np.round(L_filt/sampling_in))
    if Nparzen%2 == 0:
        Nparzen += 1    
    print("Nb of points OBP kernel: %d" % Nparzen)
    if kernel == "bharris":
        w_obp = sg.blackmanharris(Nparzen) # parzen of 41 points if input sampling is 25 m (kernel length is ~1 km)
    else:        
        w_obp = sg.parzen(Nparzen) # parzen of 41 points if input sampling is 25 m (kernel length is ~1 km)
    w_obp /= np.sum(w_obp)
    x_axis = np.arange(-(len(w_obp)-1)/2, (len(w_obp)-1)/2 + 1)*sampling_in

    # OBP spectrum
    
    if type(f_axis) != np.ndarray:
        if f_axis == None:
            f_obp, S_obp = sg.freqz(w_obp, fs=1/sampling_in)
        else:
            f_obp, S_obp = sg.freqz(w_obp, fs=1/sampling_in, worN=f_axis)
    else:
        f_obp, S_obp = sg.freqz(w_obp, fs=1/sampling_in, worN=f_axis)
    S_obp = np.abs(S_obp)**2

    if plot_flag:
        fig, ax = plt.subplots(1, 2, figsize=(11, 4))
        ax[0].plot(x_axis, w_obp/np.max(w_obp), ".-")
        ax[1].plot(f_obp, 10*np.log10(S_obp))
        ax[0].grid()
        ax[0].set_xlabel("[km]")
        ax[0].set_title("%s window (not normalized)" % kernel)
        ax[1].grid()
        ax[1].set_xlabel("freq [1/km]")
        ax[1].set_ylabel("dB [m**2.km]")
        plt.show()
    
    return x_axis, w_obp, f_obp, S_obp


In [ ]:
# Defines the spectral response H assocaited to SWOT on board processing

fx_wreg=kran*1000/2/numpy.pi
fy_wreg=kazi*1000/2/numpy.pi
kxr2, kyr2 = np.meshgrid(kran,kazi,indexing='ij') 
kn=np.sqrt(kxr2**2+kyr2**2)*1000

from  lib_filters_obp import *
x_xt, w_xt, f_xt, H_xt = get_obp_filter(L_filt = 0.980, f_axis = fx_wreg, plot_flag = False, kernel="parzen")
x_at, w_at, f_at, H_at = get_obp_filter(L_filt = 1, f_axis = fy_wreg, plot_flag = False, kernel="bharris")
H = np.transpose(np.repeat(np.array([H_xt]), len(H_at), axis=0).T * np.repeat(np.array([H_at]), len(H_xt), axis=0))
H2 = H**2

In [ ]:
fig = plt.figure(figsize = (12,10))
cut = int(periodo_size/ct)
plt.imshow((numpy.flipud(numpy.abs(H[cut:-cut,cut:-cut]))), extent=[kran[cut-1], kran[-cut],
            kazi[-cut], kazi[cut-1]], aspect='auto',cmap='jet')

kcircle=[2*pi/1000,2*pi/800, 2*pi/600, 2*pi/400]#, 2*pi/200]#, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':w')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.001), kcirstr, ha='center', va='top',fontsize=None,color='white')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('OBP spectral filter H')
cbar = plt.colorbar()
cbar.ax.set_ylabel('linear scale')

In [ ]:
spech = spec/H
fig = plt.figure(figsize = (12,10))
cut = int(periodo_size/ct)
plt.imshow(scipy.ndimage.gaussian_filter(numpy.log(numpy.flipud(numpy.abs(spech[cut:-cut+1,cut:-cut+1]))),0), extent=[kran[cut-1], kran[-cut],
            kazi[-cut], kazi[cut-1]], aspect='auto',cmap='jet')

kcircle=[2*pi/1000,2*pi/800, 2*pi/600, 2*pi/500]#, 2*pi/200]#, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':k')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, (-kcir+.0002), kcirstr, ha='center', va='top',fontsize=None,color='black')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('SSH spec / H')
cbar = plt.colorbar()
cbar.ax.set_ylabel('log scale')

In [ ]:
spech = spec/H
fig = plt.figure(figsize = (12,10))
cut = int(periodo_size/ct)
plt.imshow(medfilt(numpy.flipud(numpy.abs(spech[cut:-cut+1,cut:-cut+1])),3), extent=[kran[cut-1], kran[-cut],
            kazi[-cut], kazi[cut-1]], aspect='auto',cmap='jet')

kcircle=[2*pi/1000,2*pi/800, 2*pi/600, 2*pi/500]#, 2*pi/200]#, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':w')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.001), kcirstr, ha='center', va='top',fontsize=None,color='white')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('SSH spec / H')
cbar = plt.colorbar()
cbar.ax.set_ylabel('linear scale')

In [ ]:
fig = plt.figure(figsize = (12,10))
cut = int(periodo_size/ct)
cohtsh = '0.6'
mask = ((cohf > float(cohtsh)))
plt.imshow((numpy.flipud(numpy.abs(mask[cut:-cut+1,cut:-cut+1]))), extent=[kran[cut-1], kran[-cut],
            kazi[-cut], kazi[cut-1]], aspect='auto',cmap='jet',vmax = 1.9)

kcircle=[2*pi/1000,2*pi/800, 2*pi/600, 2*pi/500]#, 2*pi/200]#, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':w')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.001), kcirstr, ha='center', va='top',fontsize=None,color='white')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('Maximum coherence Mask (> '+cohtsh+')                                      ')
cbar = plt.colorbar()
cbar.ax.set_ylabel('lin scale')

In [ ]:
hs = 4*np.sqrt(np.sum(np.abs(mask[cut:-cut+1,cut:-cut+1]*spech[cut:-cut+1,cut:-cut+1]))*dkran*dkazi)
hs